## Using R's Nblast in Python
Tested for PyMaid version 0.3

This notebook assumes that you have successfully installed and tested all required packages (`nat` and `elmr`) in R (i.e. nblast works in R)

First, load and initialize required modules

In [1]:
from pymaid import pymaid, plot, rmaid

remote_instance = pymaid.CatmaidInstance( 'url', 'http_user', 'http_pw', 'token' )

2017-06-29 16:26:06,406 - pymaid.pymaid - INFO - CATMAID instance created. See help(CatmaidInstance) to learn how to define globally.


You can load neurons, edit them (e.g. prune) and pass them to the nblast wrapper directly. In this example, we will keep it simple and just blast a unedited neuron: a projection neuron with skeleton ID `16`

See `help(rmaid.nblast)` for details.

In [2]:
nbl_res = rmaid.nblast( 16, remote_instance = remote_instance )

2017-06-29 16:26:08,822 - pymaid.rmaid - INFO - DPS database not explicitly provided. Loading local FlyCircuit DB from dpscanon.rds
2017-06-29 16:26:17,327 - pymaid.rmaid - INFO - Blasting neuron...
2017-06-29 16:27:28,147 - pymaid.rmaid - INFO - Blasting done in 79 seconds


`nbl_res` is instance of the `rmaid.nbl_results` class. It holds all data from the nblasting and offers a (growing) number functions to do stuff with the results. See the help:

In [3]:
help(nbl_res)

Help on nbl_results in module pymaid.rmaid object:

class nbl_results(builtins.object)
 |  Class that holds nblast results and contains wrappers that allow easy
 |  plotting.    
 |  
 |  Data stored in class:
 |  --------------------
 |  self.res :      pandas Dataframe holding top N results
 |  self.sc :       original RNblast forward scores 
 |  self.scr :      original R Nblast reverse scores (Top N only)
 |  self.neuron :   the neuron that was nblasted transformed into reference space
 |  self.xdp :      dotproduct of the transformed neuron
 |  self.param :    dict holding parameters used for nblasting
 |  self.db :       dotproduct database as R object "neuronlistfh"
 |  self.date :     time of nblasting
 |  
 |  Class methods
 |  ------------
 |  plot() :        plots results. See help(nbl_results.plot) for details.
 |  get_dps():      get dotproducts for subset of self.db
 |  sort():         sorts results by given column (gene_name, forward_score,
 |                  reverse_sc

Here is an example on how to sort and then access the results

In [9]:
#Sort by mean score ((forward+reverse)/2)
nbl_res.sort( 'mu_score' )
#Check top results
nbl_res.res.head()

gene_name  forward_score  reverse_score  mu_score
0  DvGlutMARCM-F003693_seg001       0.503531       0.535153  0.519342
1     npfMARCM-F000044_seg001       0.531732       0.490217  0.510974
2     FruMARCM-F000734_seg001       0.458246       0.540427  0.499337
3     FruMARCM-M002622_seg001       0.493541       0.494606  0.494073
4  DvGlutMARCM-F002798_seg001       0.540944       0.445927  0.493436

`nbl_res` also contains a wrapper that uses `pymaid.plot.plot3d` to generate results much like in R. Pymaid's `plot3d` can use two different backends: `vispy` (default) which opens a window much like R's `plot3d()`, and `plotly` that renders in the browser. Because it is fairly easy to embedd `plotly` in Jupyiter notebooks, we will use that for this example. Note that you have to run the code, otherwise the cell below will be empty!

In [10]:
import plotly.offline as pyoff

#We need to initialize plotly for interactive rendering with Jupyter notebooks
from plotly.offline import init_notebook_mode
init_notebook_mode(connected=True)

In [17]:
fig = nbl_res.plot( hits=5, backend='plotly', fig_width = 1100)

2017-06-29 16:39:02,907 - pymaid.rmaid - WARNING - Please provide a remote instance if you want to add neuron name.
2017-06-29 16:39:03,050 - pymaid.plot - INFO - Preparing neurons for plotting
2017-06-29 16:39:06,355 - pymaid.plot - INFO - Done. Plotted 16153 nodes and 0 connectors
2017-06-29 16:39:06,355 - pymaid.plot - INFO - Use plotly.offline.plot(fig, filename="3d_plot.html") to plot. Optimised for Google Chrome.


In [18]:
pyoff.iplot(fig)